In [15]:
import os

os.environ["KERAS_BACKEND"] = "tensorflow"

In [16]:
import tensorflow as tf

devices = tf.config.list_physical_devices()
print("\nDevices: ", devices)

gpus = tf.config.list_physical_devices('GPU')
if gpus:
    details = tf.config.experimental.get_device_details(gpus[0])
    print("GPU details: ", details)


Devices:  [PhysicalDevice(name='/physical_device:CPU:0', device_type='CPU'), PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]
GPU details:  {'device_name': 'METAL'}


In [17]:
from keras.models import Sequential
from keras.layers import Dense

import plotly.express as px
import keras_tuner as kt
import pandas as pd
import keras

In [18]:
N_SKUIDs_predicted = 5

In [19]:
clients = pd.read_pickle("data/parsed/clients.pkl")
transactions = pd.read_pickle("data/parsed/modeling_transactions.pkl")

In [20]:
clients = (pd.concat([
        clients[["POC"]],
        pd.get_dummies(clients["BussinessSegment"], dtype=int),
    ],
    axis=1
    )
    .set_index(["POC"])
)

In [21]:
x0 = transactions.copy()
x1 = transactions.copy()
x2 = transactions.copy()
x3 = transactions.copy()

x0["ORDER_RANK"] += 0
x1["ORDER_RANK"] += 1
x2["ORDER_RANK"] += 2
x3["ORDER_RANK"] += 3

x0 = x0.set_index(["POC","ORDER_RANK"])
x1 = x1.set_index(["POC","ORDER_RANK"])
x2 = x2.set_index(["POC","ORDER_RANK"])
x3 = x3.set_index(["POC","ORDER_RANK"])

x0.columns = pd.Index([str(c) + "_x0" for c in x0.columns], name="SKU_ID")
x1.columns = pd.Index([str(c) + "_x1" for c in x1.columns], name="SKU_ID")
x2.columns = pd.Index([str(c) + "_x2" for c in x2.columns], name="SKU_ID")
x3.columns = pd.Index([str(c) + "_x3" for c in x3.columns], name="SKU_ID")

y0 = transactions.copy()
y0["ORDER_RANK"] += -1
y0 = y0.set_index(["POC","ORDER_RANK"])
y0.columns = pd.Index(
    [str(c) + "_y" for c in y0.columns],
    name="SKU_ID"
)

In [22]:
df = (x0
    .merge(x1, left_index=True, right_index=True, how="inner")
    .merge(x2, on=["POC","ORDER_RANK"], how="inner")
    .merge(x3, on=["POC","ORDER_RANK"], how="inner")
    .merge(y0, left_index=True, right_index=True, how="inner")
    .merge(clients, left_index=True, right_index=True, how="inner")
)

df_test = df.sample(frac=0.2)
df_train = df.merge(df_test[[]], left_index=True, right_index=True, indicator=True, how="left")
df_train = df_train[df_train["_merge"] == "left_only"].drop(columns="_merge").copy()


print(df_test.shape, df_train.shape)

(5563, 759) (22251, 759)


In [23]:
x_columns = [c for c in df_train.columns if "_y" not in c]
y_columns = [c for c in df_train.columns if "_y" in c]

x_test, y_test = df_test[x_columns].copy(), df_test[y_columns].copy()
x_train, y_train = df_train[x_columns].copy(), df_train[y_columns].copy()

y_test.columns = pd.Index(
    [c.replace("_y","") for c in y_columns],
    name="SKU_ID"
)

y_train.columns = pd.Index(
    [c.replace("_y","") for c in y_columns],
    name="SKU_ID"
)

print(x_test.shape, x_train.shape)
print(y_test.shape, y_train.shape)

(5563, 608) (22251, 608)
(5563, 151) (22251, 151)


In [24]:
class MyHyperModel(kt.HyperModel):
    def build(self, hp):
        model = Sequential([
                Dense(
                    y_train.shape[1],
                    activation="tanh",
                    # activation=hp.Choice("activation", ["relu", "tanh"])
                ),
                Dense(
                    y_train.shape[1],
                    activation="tanh",
                    # activation=hp.Choice("activation", ["relu", "tanh"])
                )
            ]
        )

        # if hp.Boolean("3rd_layer"):
        #     model.add(
        #         Dense(
        #             y_train.shape[1],
        #             activation="tanh",
        #             # activation=hp.Choice("activation", ["relu", "tanh"])
        #         )
        #     )

        model.compile(
            loss="mean_squared_error",
            metrics=[keras.metrics.MeanSquaredError()],
            optimizer=keras.optimizers.Adam(learning_rate=1e-4),
            # optimizer = keras.optimizers.Adam(
            #     hp.Choice(
            #         'learning_rate',
            #         values = [
            #             #1e-2,
            #             1e-3,
            #             1e-4,
            #             1e-5,
            #         ]
            #     )
            # )
        )
        return model

    def fit(self, hp, model, *args, **kwargs):
        return model.fit(
            *args,
            epochs=16,
            # epochs = hp.Choice("epochs", [2, 4, 8, 16]),
            batch_size=32,
            # batch_size = hp.Choice("batch_size", [32, 64, 128, 256]),
            **kwargs,
        )

tuner = kt.GridSearch(
    MyHyperModel(),
    overwrite=True,
    directory="models/dnn",
    project_name="dnn",
    objective=kt.Objective("val_mean_squared_error", direction="min"),
)

tuner.search(
    x_train.values,
    y_train.values,
    validation_data=(x_test, y_test)
)

tuner.results_summary()

best_model = tuner.get_best_models()[0]

Trial 1 Complete [00h 00m 53s]
val_mean_squared_error: 0.030711205676198006

Best val_mean_squared_error So Far: 0.030711205676198006
Total elapsed time: 00h 00m 53s
Results summary
Results in models/dnn/dnn
Showing 10 best trials
Objective(name="val_mean_squared_error", direction="min")

Trial 0000 summary
Hyperparameters:
default configuration
Score: 0.030711205676198006


In [25]:
y_test_predicted = pd.DataFrame(
    best_model.predict(x_test.values),
    columns = y_test.columns,
    index=y_test.index
)

y_train_predicted = pd.DataFrame(
    best_model.predict(x_train.values),
    columns = y_train.columns,
    index=y_train.index
)


y_test_predicted = y_test_predicted.stack()
y_test_predicted.name = "predicted_value"
y_test_predicted = y_test_predicted.reset_index()
y_test_predicted = y_test_predicted.sort_values(["POC","ORDER_RANK","predicted_value"], ascending=False)
y_test_predicted["SKUID_PREDICTION_RANK"] = y_test_predicted.groupby(["POC","ORDER_RANK"])["predicted_value"].rank(method="first", ascending=False).astype(int)
y_test_predicted = y_test_predicted[y_test_predicted["SKUID_PREDICTION_RANK"] <= N_SKUIDs_predicted].copy()

y_train_predicted = y_train_predicted.stack()
y_train_predicted.name = "predicted_value"
y_train_predicted = y_train_predicted.reset_index()
y_train_predicted = y_train_predicted.sort_values(["POC","ORDER_RANK","predicted_value"], ascending=False)
y_train_predicted["SKUID_PREDICTION_RANK"] = y_train_predicted.groupby(["POC","ORDER_RANK"])["predicted_value"].rank(method="first", ascending=False).astype(int)
y_train_predicted = y_train_predicted[y_train_predicted["SKUID_PREDICTION_RANK"] <= N_SKUIDs_predicted].copy()

105/174 [=================>............] - ETA: 0s

2024-07-28 17:54:19.564113: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


696/696 [==============================] - 1s 1ms/step


In [26]:
px.histogram(y_test_predicted, x="predicted_value", color="SKUID_PREDICTION_RANK", barmode="overlay", histnorm="probability", title="test").show()
px.histogram(y_train_predicted, x="predicted_value", color="SKUID_PREDICTION_RANK", barmode="overlay", histnorm="probability", title="train").show()

In [27]:
y_test = y_test.stack()
y_test = y_test[y_test == 1].copy()
y_test.name = "present_values"
y_test = y_test.reset_index()

y_train = y_train.stack()
y_train = y_train[y_train == 1].copy()
y_train.name = "present_values"
y_train = y_train.reset_index()

Both is good, left_only is bad

In [28]:
N_ROUNDING = 2

test_accuracy = (y_test_predicted
    .merge(y_test,
        on=["POC","ORDER_RANK","SKU_ID"],
        how="left",
        indicator=True
    )
)

train_accuracy = (y_train_predicted
    .merge(y_train,
        on=["POC","ORDER_RANK","SKU_ID"],
        how="left",
        indicator=True
    )
)

test_accuracy["accurate"] = test_accuracy["_merge"] == "both"
train_accuracy["accurate"] = train_accuracy["_merge"] == "both"

counts = test_accuracy[["SKUID_PREDICTION_RANK","accurate"]].value_counts().rename("counts").reset_index()
total_counts = test_accuracy[["SKUID_PREDICTION_RANK"]].value_counts().rename("total_counts").reset_index()
test_accuracy_byPredictionRank = counts.merge(total_counts, on=["SKUID_PREDICTION_RANK"], how="left")
test_accuracy_byPredictionRank["accuracy"] = (test_accuracy_byPredictionRank["counts"] / test_accuracy_byPredictionRank["total_counts"]).round(N_ROUNDING)
test_accuracy_byPredictionRank = test_accuracy_byPredictionRank.set_index(["SKUID_PREDICTION_RANK","accurate"]).sort_index()
test_accuracy_byPredictionRank.columns.name = "test"

counts = train_accuracy[["SKUID_PREDICTION_RANK","accurate"]].value_counts().rename("counts").reset_index()
total_counts = train_accuracy[["SKUID_PREDICTION_RANK"]].value_counts().rename("total_counts").reset_index()
train_accuracy_byPredictionRank = counts.merge(total_counts, on=["SKUID_PREDICTION_RANK"], how="left")
train_accuracy_byPredictionRank["accuracy"] = (train_accuracy_byPredictionRank["counts"] / train_accuracy_byPredictionRank["total_counts"]).round(N_ROUNDING)
train_accuracy_byPredictionRank = train_accuracy_byPredictionRank.set_index(["SKUID_PREDICTION_RANK","accurate"]).sort_index()
train_accuracy_byPredictionRank.columns.name = "train"

display(test_accuracy_byPredictionRank)
display(train_accuracy_byPredictionRank)


test_accuracy_agg = test_accuracy[["accurate"]].value_counts().rename("counts").reset_index()
test_accuracy_agg["total_counts"] = len(test_accuracy)
test_accuracy_agg["accuracy"] = (test_accuracy_agg["counts"] / test_accuracy_agg["total_counts"]).round(N_ROUNDING)
test_accuracy_agg = test_accuracy_agg.set_index(["accurate"]).sort_index()
test_accuracy_agg.columns.name = "test"

train_accuracy_agg = train_accuracy[["accurate"]].value_counts().rename("counts").reset_index()
train_accuracy_agg["total_counts"] = len(train_accuracy)
train_accuracy_agg["accuracy"] = (train_accuracy_agg["counts"] / train_accuracy_agg["total_counts"]).round(N_ROUNDING)
train_accuracy_agg = train_accuracy_agg.set_index(["accurate"]).sort_index()
train_accuracy_agg.columns.name = "train"

display(test_accuracy_agg)
display(train_accuracy_agg)

test                            counts  total_counts  accuracy
SKUID_PREDICTION_RANK accurate                                
1                     False       2515          5563      0.45
                      True        3048          5563      0.55
2                     False       3180          5563      0.57
                      True        2383          5563      0.43
3                     False       3664          5563      0.66
                      True        1899          5563      0.34
4                     False       3956          5563      0.71
                      True        1607          5563      0.29
5                     False       4132          5563      0.74
                      True        1431          5563      0.26

train                           counts  total_counts  accuracy
SKUID_PREDICTION_RANK accurate                                
1                     False       9460         22251      0.43
                      True       12791         22251      0.57
2                     False      12513         22251      0.56
                      True        9738         22251      0.44
3                     False      14221         22251      0.64
                      True        8030         22251      0.36
4                     False      15293         22251      0.69
                      True        6958         22251      0.31
5                     False      16135         22251      0.73
                      True        6116         22251      0.27

test      counts  total_counts  accuracy
accurate                                
False      17447         27815      0.63
True       10368         27815      0.37

train     counts  total_counts  accuracy
accurate                                
False      67622        111255      0.61
True       43633        111255      0.39